# Movie Recommendation Engine Based on Collaborative Filtering

---

Recommender System is a system that seeks to predict or filter preferences according to the user’s choices. Recommender systems are utilized in a variety of areas including movies, music, news, books, research articles, search queries, social tags, and products in general.

**Recommender systems produce a list of recommendations in any of the two ways:**
1. **Collaborative filtering**

2. **Content-based filtering** (Uses series of discrete characteristics of an item in order to recommend additional items with similar properties)

**In this problem we'll be using "Collaborative filtering"!**

In [1]:
## Importing all required libraries...
import pandas as pd
import numpy as np

pd.options.display.max_rows = None
pd.options.display.max_columns = None

In [2]:
## Loading User data....
data_raw = pd.read_csv('ratings.csv')
data_raw.head()

userId  movieId  rating   timestamp
0       1       16     4.0  1217897793
1       1       24     1.5  1217895807
2       1       32     4.0  1217896246
3       1       47     4.0  1217896556
4       1       50     4.0  1217896523

In [3]:
print("Dimensions of the above data is :" , data_raw.shape)

Dimensions of the above data is : (105339, 4)


In [4]:
## Loading movie data....
data_movie = pd.read_csv('movies.csv')
data_movie.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [5]:
print("Dimensions of the above data is :" , data_movie.shape)

Dimensions of the above data is : (10329, 3)


In [6]:
## Merging Movie data with raw data....
data = pd.merge(data_raw , data_movie , on = 'movieId' , how = 'left')

In [7]:
data.head()

userId  movieId  rating   timestamp  \
0       1       16     4.0  1217897793   
1       1       24     1.5  1217895807   
2       1       32     4.0  1217896246   
3       1       47     4.0  1217896556   
4       1       50     4.0  1217896523   

                                       title                   genres  
0                              Casino (1995)              Crime|Drama  
1                              Powder (1995)             Drama|Sci-Fi  
2  Twelve Monkeys (a.k.a. 12 Monkeys) (1995)  Mystery|Sci-Fi|Thriller  
3                Seven (a.k.a. Se7en) (1995)         Mystery|Thriller  
4                 Usual Suspects, The (1995)   Crime|Mystery|Thriller

## Preprocessing "Genre" :

In [8]:
for i in range(data.shape[0]):
    temp = data['genres'][i]
    temp = temp.replace('|' , ' ')
    temp = temp.replace('-' , '')
    data['genres'][i] = temp

C:\Anaconda\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


In [9]:
data.head()

userId  movieId  rating   timestamp  \
0       1       16     4.0  1217897793   
1       1       24     1.5  1217895807   
2       1       32     4.0  1217896246   
3       1       47     4.0  1217896556   
4       1       50     4.0  1217896523   

                                       title                  genres  
0                              Casino (1995)             Crime Drama  
1                              Powder (1995)             Drama SciFi  
2  Twelve Monkeys (a.k.a. 12 Monkeys) (1995)  Mystery SciFi Thriller  
3                Seven (a.k.a. Se7en) (1995)        Mystery Thriller  
4                 Usual Suspects, The (1995)  Crime Mystery Thriller

In [10]:
from sklearn.feature_extraction.text import CountVectorizer

BOW = CountVectorizer(max_features = 15 , lowercase = False)
BOW.fit(data['genres'])

## Creating a data frame for top 15 genres....
Genres = pd.DataFrame(data = BOW.transform(data['genres']).toarray() , columns = BOW.get_feature_names())
Genres.head()

Action  Adventure  Animation  Children  Comedy  Crime  Drama  Fantasy  \
0       0          0          0         0       0      1      1        0   
1       0          0          0         0       0      0      1        0   
2       0          0          0         0       0      0      0        0   
3       0          0          0         0       0      0      0        0   
4       0          0          0         0       0      1      0        0   

   Horror  Musical  Mystery  Romance  SciFi  Thriller  War  
0       0        0        0        0      0         0    0  
1       0        0        0        0      1         0    0  
2       0        0        1        0      1         1    0  
3       0        0        1        0      0         1    0  
4       0        0        1        0      0         1    0

In [11]:
## Joining the created genres data frame to main data frame....
df = data.join(Genres)

In [12]:
## Dictionary for Movies with respect to their IDs.....
movie_dict = data_movie[['movieId' , 'title']].set_index('movieId').T.to_dict('records')

<hr> 

## <center>Creating a Recommendation engine Based on Collabrative Filtering:</center>

- **What Is Collaborative Filtering?** 
  - Collaborative filtering is a technique that can filter out items that a user might like on the basis of reactions by similar users. It works by searching a large group of people and finding a smaller set of users with tastes similar to a particular user.

In [13]:
## Making pivot table with index as "Movie ID" , Columns as "User ID" and values as "Rating"......
data_transformed = pd.pivot_table(data , values = 'rating' , index = 'movieId' , columns = 'userId' , fill_value=0)
data_transformed.head(5)

userId   1    2    3    4    5    6    7    8    9    10   11   12   13   14   \
movieId                                                                         
1        0.0    5    0    0  4.0  0.0  0.0    5    0  0.0    4  0.0  0.0    4   
2        0.0    0    0    0  0.0  0.0  0.0    0    0  0.0    0  0.0  0.0    0   
3        0.0    2    0    0  0.0  0.0  0.0    4    3  0.0    0  3.0  0.0    3   
4        0.0    0    0    0  0.0  0.0  0.0    0    0  0.0    0  0.0  0.0    0   
5        0.0    3    3    0  0.0  0.0  0.0    3    0  0.0    0  0.0  0.0    3   

userId   15   16   17   18   19   20   21   22   23   24   25   26   27   28   \
movieId                                                                         
1        0.0    0  5.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0    3   
2        0.0    3  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0    0   
3        0.0    0  0.0  0.0  0.0  0.0  0.0  2.5  0.0    0    2  0.0    0    0   
4        0.0    0  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0    0   
5        0.0    0  0.0  0.0  0.0  0.0  0.0  2.5  0.0    0    0  0.0    0    0   

userId   29   30   31   32   33   34   35   36   37   38   39   40   41   42   \
movieId                                                                         
1          4  4.5    4    4    0    0    0    0  0.0  5.0    0    0  0.0  0.0   
2          4  0.0    4    3    0    0    0    0  0.0  2.0    0    0  0.0  0.0   
3          0  0.0    0    4    0    0    3    0  0.0  0.0    0    0  0.0  0.0   
4          0  0.0    0    0    0    0    0    0  0.0  0.0    0    0  0.0  0.0   
5          0  0.0    0    0    0    3    3    0  0.0  0.0    0    0  0.0  5.0   

userId   43   44   45   46   47   48   49   50   51   52   53   54   55   56   \
movieId                                                                         
1        0.0  1.5  4.0    0    0  0.0    0    4    0  3.0  0.0  3.0  0.0    0   
2        0.0  0.0  0.0    0    0  0.0    0    0    0  0.0  0.0  4.0  0.0    0   
3        0.0  0.0  0.0    0    0  0.0    0    0    0  0.0  0.0  0.0  0.0    0   
4        0.0  0.0  0.0    0    0  0.0    0    0    0  0.0  0.0  0.0  0.0    0   
5        0.0  0.0  0.0    0    0  0.0    0    0    0  0.0  0.0  0.0  0.0    0   

userId   57   58   59   60   61   62   63   64   65   66   67   68   69   70   \
movieId                                                                         
1        0.0  0.0  0.0  3.0  0.0  2.0  0.0  0.0    0    0  0.0    0  4.0  4.0   
2        0.0  0.0  0.0  0.0  0.0  1.5  0.0  0.0    0    0  0.0    0  0.0  0.0   
3        0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0    0    0  0.0    0  0.0  0.0   
4        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0  0.0  0.0   
5        0.0  0.0  0.0  0.0  0.0  3.5  0.0  0.0    0    0  0.0    0  0.0  0.0   

userId   71   72   73   74   75   76   77   78   79   80   81   82   83   84   \
movieId                                                                         
1        4.5    5    0  2.0    0  0.0  0.0    0  0.0  0.0    4  0.0  3.5  3.0   
2        0.0    0    0  0.0    0  0.0  0.0    0  0.0  0.0    0  0.0  0.0  0.0   
3        0.0    3    0  0.0    0  0.0  0.0    0  0.0  0.0    0  0.0  0.0  0.0   
4        0.0    0    0  0.0    0  0.0  0.0    0  0.0  3.5    0  0.0  0.0  0.0   
5        0.0    0    0  0.0    0  0.0  0.0    0  0.0  0.0    0  0.0  1.5  0.0   

userId   85   86   87   88   89   90   91   92   93   94   95   96   97   98   \
movieId                                                                         
1        0.0  3.0  0.0  4.5  4.0    0    0    0    4  0.0    0    5  3.5    0   
2        0.0  0.0  0.0  4.5  0.0    0    0    0    0  0.0    0    0  4.0    0   
3        0.0  0.0  0.0  0.0  0.0    0    0    0    3  0.0    0    4  0.0    0   
4        0.0  0.0  0.0  0.0  0.0    0    0    0    0  0.0    0    0  0.0    0   
5        0.0  0.0  0.0  0.0  2.0    0    0    0    3  0.0    0    3  0.0    0   

userId   99   100  101  

In [14]:
## Applying dimensionality reduction.....
from sklearn.decomposition import TruncatedSVD

dim_red = TruncatedSVD(n_components = 100)
reduced_data = data = dim_red.fit_transform(data_transformed)
print("Dimensions of Reduced matrix is :" , reduced_data.shape)

Dimensions of Reduced matrix is : (10325, 100)


In [15]:
## Creating correlation matrix....
corre_matrix = np.corrcoef(reduced_data)
corr_matrix = pd.DataFrame(data = corre_matrix , columns = data_transformed.index , 
                           index = data_transformed.index)
corr_matrix.head()

movieId    1         2         3         4         5         6         7       \
movieId                                                                         
1        1.000000  0.509344  0.459364  0.201757  0.512427  0.526899  0.474637   
2        0.509344  1.000000  0.422241  0.260206  0.353143  0.470488  0.373703   
3        0.459364  0.422241  1.000000  0.301748  0.712464  0.491158  0.489369   
4        0.201757  0.260206  0.301748  1.000000  0.225884  0.291315  0.161816   
5        0.512427  0.353143  0.712464  0.225884  1.000000  0.389068  0.641105   

movieId    8         9         10        11        12        13        14      \
movieId                                                                         
1        0.159370  0.258857  0.468440  0.439675  0.289887  0.173691  0.397439   
2        0.188193  0.132506  0.606080  0.458030  0.310366  0.246663  0.190429   
3        0.289891  0.532786  0.243000  0.389446  0.427156  0.220070  0.470393   
4        0.372942  0.198070  0.249200  0.310289  0.122887  0.182040 -0.049994   
5        0.295743  0.401463  0.233571  0.399099  0.281508  0.145277  0.514382   

movieId    15        16        17        18        19        20        21      \
movieId                                                                         
1        0.217359  0.405229  0.529682  0.288842  0.400711  0.207586  0.441150   
2        0.296875  0.500584  0.322625  0.269221  0.633369  0.322985  0.491396   
3        0.217511  0.267287  0.348226  0.261443  0.315914  0.198354  0.320418   
4        0.446861  0.261149  0.190795  0.273664  0.199093  0.416387  0.369745   
5        0.265268  0.280993  0.448180  0.245274  0.321771  0.071150  0.322804   

movieId    22        23        24        25        26        27        28      \
movieId                                                                         
1        0.327758  0.284615  0.301064  0.498775  0.278344  0.128450  0.214928   
2        0.341255  0.269046  0.452349  0.375178  0.208768  0.329816  0.216811   
3        0.338906  0.185028  0.472230  0.529277  0.294910  0.202236  0.177212   
4        0.426415  0.243662  0.218902  0.293852  0.033155  0.618431  0.414650   
5        0.347549  0.232300  0.410206  0.505821  0.271594  0.182619  0.183282   

movieId    29        30        31        32        33        34        35      \
movieId                                                                         
1        0.386295  0.149148  0.331214  0.562984  0.082607  0.566373  0.079932   
2        0.251075  0.255626  0.471127  0.469012  0.126190  0.498105  0.242258   
3        0.341140  0.181609  0.367610  0.371024 -0.022605  0.245251  0.106059   
4        0.166573  0.361116  0.462094  0.240160 -0.030889  0.283294  0.366221   
5        0.212217  0.132465  0.353285  0.315035  0.004922  0.362311  0.109529   

movieId    36        39        40        41        42        43        44      \
movieId                                                                         
1        0.518433  0.489118  0.156854  0.292804  0.120361  0.271411  0.385304   
2        0.334752  0.545766  0.235625  0.186599  0.110863  0.153983  0.548239   
3        0.544260  0.390728  0.233690  0.230506  0.120240  0.394403  0.350374   
4        0.193634  0.268246  0.406541  0.439856  0.336596  0.372140  0.403578   
5        0.433550  0.521285  0.140091  0.249894  0.078048  0.262842  0.212438   

movieId    45        46        47        48        49        50        52      \
movieId                                                                         
1        0.293639  0.136192  0.545667  0.396332  0.102763  0.591634  0.450719   
2        0.287683  0.304381  0.494302  0.518072  0.185103  0.456106  0.227790   
3        0.278110  0.273586  0.204579  0.259880 -0.020224  0.172231  0.482847   
4        0.393256  0.575453  0.234909  0.474823  0.452407  0.266661  0.320206   
5        0.307999  0.266929  0.249440  0.251763 -0.019302  0.227618  0.449515   

movieId    53        54 

In [18]:
## Taking input of 'Movie ID' of last watched movies.....
movie = input("Enter the Movie ID of your last watched movie :" )

Enter the Movie ID of your last watched movie :601


In [19]:
## Finding all highly correlated movies to recommend....
corr_scores = pd.Series(corr_matrix[int(movie)])
corr_scores.index = corr_matrix.index
corr_scores.sort_values(ascending = False , inplace = True)

## Creating recommend product list by taking top 10 most correlated products....
recommend = list(corr_scores.head(20).index)
if int(movie) in recommend:
    recommend.remove(int(movie))

## Priniting list of all recommended products are....
print("Top 10 Recommended Movies are: \n" , pd.DataFrame(data = pd.Series(recommend[0:10]).map(movie_dict[0]) , 
                                                        columns = ['Movies']))

Top 10 Recommended Movies are: 
                                               Movies
0                                   Artemisia (1997)
1                           Margaret's Museum (1995)
2  Red Firecracker, Green Firecracker (Pao Da Shu...
3                               Mrs. Dalloway (1997)
4                              Dangerous Game (1993)
5                   Baton Rouge (Bâton rouge) (1988)
6                     Run of the Country, The (1995)
7                            Nothing Personal (1995)
8                  Beans of Egypt, Maine, The (1994)
9                           Grace of My Heart (1996)


<hr>

# <center><U>Recommendation based on Movie Genre:</U></center>

In [21]:
list_of_genres = BOW.get_feature_names()
print(pd.DataFrame(data = list_of_genres , columns = ['Genre']))
genre = input("Enter your preferred genre :")

        Genre
0      Action
1   Adventure
2   Animation
3    Children
4      Comedy
5       Crime
6       Drama
7     Fantasy
8      Horror
9     Musical
10    Mystery
11    Romance
12      SciFi
13   Thriller
14        War
Enter your preferred genre :Action


#### Making seperate pivot table for collaborative filtering:

In [22]:
ind = np.where(df[genre]==1 , True , False)
df1 = df.loc[ind , ]

## Making pivot table with index as "Movie ID" , Columns as "User ID" and values as "Rating"......
data_transformed_genre = pd.pivot_table(df1 , values = 'rating' , index = 'movieId' , columns = 'userId' , fill_value=0)
data_transformed_genre.head(5)

userId   1    2    3    4    5    6    7    8    9    10   11   12   13   14   \
movieId                                                                         
6        0.0    0    0    0  0.0  0.0  0.0    0    4  0.0    0    0  0.0    0   
9        0.0    0    0    0  0.0  0.0  0.0    0    0  0.0    0    0  0.0    0   
10       0.0    0    0    0  0.0  0.0  4.0    0    3  0.0    3    0  0.0    0   
15       0.0    0    0    0  0.0  0.0  0.0    0    0  0.0    0    0  0.0    0   
20       0.0    0    0    0  0.0  0.0  0.0    0    0  0.0    0    0  3.5    0   

userId   15   16   17   18   19   20   21   22   23   24   25   26   27   28   \
movieId                                                                         
6        0.0    0  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0    0   
9        0.0    4  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0    0   
10       0.0    0  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0    3   
15       0.0    0  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0    0   
20       0.0    0  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0    0    0   

userId   29   30   31   32   33   34   35   36   37   38   39   40   41   42   \
movieId                                                                         
6          4  0.0    4    0    0    0    5    0  0.0  0.0    0    0  0.0  0.0   
9          3  0.0    0    0    0    0    0    0  0.0  0.0    0    0  0.0  0.0   
10         4  0.0    0    5    0    0    0    3  0.0  0.0    0    0  0.0  0.0   
15         3  0.0    0    0    0    0    0    0  0.0  0.0    0    0  0.0  0.0   
20         3  0.0    0    0    0    0    0    0  0.0  0.0    0    0  0.0  0.0   

userId   43   44   45   46   47   48   49   50   51   52   53   54   55   56   \
movieId                                                                         
6        0.0  0.0  0.0    0    0  0.0    0    0    0  0.0  0.0  0.0  0.0    0   
9        0.0  0.0  0.0    0    0  0.0    0    0    0  0.0  0.0  0.0  0.0    0   
10       0.0  0.0  0.0    0    0  0.0    0    0    5  0.0  0.0  0.0  0.0    0   
15       0.0  0.0  0.0    0    0  0.0    0    0    0  0.0  0.0  0.0  0.0    0   
20       0.0  0.0  0.0    0    0  0.0    0    0    0  0.0  0.0  0.0  0.0    0   

userId   57   58   59   60   61   62   63   64   65   66   67   69   70   71   \
movieId                                                                         
6        0.0  0.0  0.0  0.0  0.0  4.5  3.0  0.0    4    0  0.0  4.5  0.0  0.0   
9        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0  0.0  0.0  0.0   
10       0.0  0.0  0.0  0.0  0.0  0.0  2.5  0.0    0    0  0.0  0.0  0.0  0.0   
15       0.0  0.0  0.0  0.0  0.0  0.0  3.5  0.0    0    0  0.0  0.0  0.0  0.0   
20       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0    0    0  0.0  0.0  0.0  0.0   

userId   72   73   74   75   76   77   78   79   80   81   83   84   85   86   \
movieId                                                                         
6          3    0  0.0    0  0.0  0.0    0  4.0  0.0    0  0.0  0.0  0.0  0.0   
9          1    0  0.0    0  0.0  0.0    0  0.0  0.0    0  0.0  0.0  0.0  0.0   
10         0    0  0.0    0  0.0  0.0    0  0.0  0.0    0  0.0  0.0  0.0  0.0   
15         0    0  0.0    0  0.0  0.0    0  0.0  0.0    0  0.0  0.0  0.0  0.0   
20         0    0  0.0    0  0.0  0.0    0  0.0  0.0    0  0.0  0.0  0.0  0.0   

userId   87   88   89   90   91   92   93   94   95   96   97   98   99   100  \
movieId                                                                         
6        4.5  4.5  0.0    0    0    0    0  0.0    0    4  0.0    0  0.0  0.0   
9        0.0  0.0  0.0    0    0    0    0  0.0    3    1  0.0    0  0.0  0.0   
10       0.0  3.5  4.0    0    0    0    0  0.0    0    0  0.0    0  0.0  0.0   
15       0.0  0.0  0.0    0    0    0    0  0.0    0    0  0.0    0  0.0  0.0   
20       0.0  0.0  0.0    0    0    0    0  0.0    0    0  0.0    0  0.0  0.0   

userId   101  102  103  

In [23]:
## Applying dimensionality reduction.....
dim_red_genre = TruncatedSVD(n_components = 80)
reduced_data_genre = data = dim_red_genre.fit_transform(data_transformed_genre)
print("Dimensions of Reduced matrix is :" , reduced_data_genre.shape)

Dimensions of Reduced matrix is : (1737, 80)


In [24]:
## Creating correlation matrix....
corre_matrix_genre = np.corrcoef(reduced_data_genre)
corr_matrix_genre = pd.DataFrame(data = corre_matrix_genre , columns = data_transformed_genre.index , 
                                 index = data_transformed_genre.index)
corr_matrix_genre.head()

movieId    6         9         10        15        20        23        42      \
movieId                                                                         
6        1.000000  0.475516  0.444910  0.345637  0.357698  0.420030  0.428875   
9        0.475516  1.000000  0.258883  0.366529  0.324655  0.235023  0.153078   
10       0.444910  0.258883  1.000000  0.360853  0.432683  0.496110  0.213918   
15       0.345637  0.366529  0.360853  1.000000  0.327237  0.400602  0.006722   
20       0.357698  0.324655  0.432683  0.327237  1.000000  0.422204  0.217250   

movieId    44        66        70        71        76        78        86      \
movieId                                                                         
6        0.354669  0.464865  0.568159  0.170128  0.496226  0.424815  0.437916   
9        0.294422  0.560925  0.240655  0.258113  0.473201  0.439120  0.443899   
10       0.574671  0.149467  0.531634  0.482513  0.265034  0.161539  0.192261   
15       0.399477  0.245559  0.321998  0.340017  0.120457  0.299442  0.350937   
20       0.421141  0.145799  0.464096  0.436141  0.540635  0.515634  0.225612   

movieId    89        95        110       112       145       151       153     \
movieId                                                                         
6        0.454519  0.652738  0.437068  0.466001  0.482639  0.470635  0.447670   
9        0.464817  0.661938  0.110575  0.473624  0.291085  0.149077  0.224484   
10       0.330923  0.475243  0.523544  0.478373  0.459334  0.367549  0.770929   
15       0.356262  0.414178  0.273418  0.179242  0.403017  0.292722  0.457527   
20       0.264035  0.372071  0.262477  0.305598  0.342994  0.279918  0.400394   

movieId    160       163       165       168       170       172       173     \
movieId                                                                         
6        0.367399  0.619409  0.546080  0.399317  0.519018  0.440418  0.500888   
9        0.283990  0.297898  0.268115  0.329442  0.252227  0.369729  0.346027   
10       0.569775  0.539260  0.677931  0.383041  0.391173  0.565733  0.562364   
15       0.428548  0.430212  0.408824  0.534999  0.442060  0.454473  0.559591   
20       0.416925  0.563636  0.362407  0.408971  0.431958  0.446347  0.531977   

movieId    181       185       198       204       208       227       236     \
movieId                                                                         
6        0.159196  0.347902  0.469973  0.395214  0.529272  0.353851  0.370942   
9        0.130782  0.177218  0.147922  0.460641  0.256422  0.407143  0.205957   
10       0.309446  0.627769  0.389333  0.568341  0.644573  0.463350  0.393355   
15       0.187851  0.354642  0.235975  0.441118  0.444142  0.528244  0.251983   
20       0.233951  0.353317  0.624757  0.608853  0.370567  0.617498  0.115586   

movieId    251       260       288       292       293       303       315     \
movieId                                                                         
6        0.235267  0.503721  0.528299  0.469686  0.549564  0.534967  0.501600   
9        0.180734  0.270469  0.115797  0.284425  0.096409  0.346603  0.429273   
10       0.183058  0.393603  0.597210  0.655257  0.434783  0.470989  0.503898   
15       0.116714  0.227034  0.227748  0.387727  0.277286  0.494461  0.562844   
20       0.220920  0.208794  0.374811  0.348433  0.286664  0.455265  0.576158   

movieId    316       327       330       338       349       353       360     \
movieId                                                                         
6        0.436978  0.362025  0.210602  0.311262  0.479114  0.585560  0.354919   
9        0.202815  0.207545  0.263652  0.207196  0.315237  0.230725  0.330843   
10       0.677670  0.322767  0.256150  0.357136  0.686463  0.516986  0.206810   
15       0.407991  0.335341  0.521752  0.300630  0.367069  0.365104  0.210946   
20       0.364093  0.464876  0.568788  0.464200  0.513284  0.420859  0.138677   

movieId    367       370

In [26]:
## Taking input of 'Movie ID' of last watched movies.....
movie = input("Enter the Movie ID of your last watched movie of '{}' Genre:".format(genre))

Enter the Movie ID of your last watched movie of 'Action' Genre:2816


In [27]:
## Finding all highly correlated movies to recommend....
corr_scores = pd.Series(corr_matrix_genre[int(movie)])
corr_scores.index = corr_matrix_genre.index
corr_scores.sort_values(ascending = False , inplace = True)

## Creating recommend product list by taking top 10 most correlated products....
recommend = list(corr_scores.head(20).index)
if int(movie) in recommend:
    recommend.remove(int(movie))

## Priniting list of all recommended products are....
print("Top 10 Recommended Movies of '{}' Genre are: \n".format(genre) , 
      pd.DataFrame(data = pd.Series(recommend[0:10]).map(movie_dict[0]) , columns = ['Movies']))

Top 10 Recommended Movies of 'Action' Genre are: 
                               Movies
0               Iron Eagle IV (1995)
1                  Iron Eagle (1986)
2    Karate Kid, Part II, The (1986)
3   Karate Kid, Part III, The (1989)
4                    Rocky IV (1985)
5  Rambo: First Blood Part II (1985)
6                   Condorman (1981)
7                   Rocky III (1982)
8                   Supergirl (1984)
9                    Freejack (1992)


# About Recommendation Engine:

### We created 2 types of models here:
- **Model 1:** It recommemds movies irrespective of movie "Genre".
- **Model 2:** It recommemds movies specific to input "Genre".